In [11]:
from ngsolve import *
from netgen.geom2d import SplineGeometry
from numpy import pi
ngsglobals.msg_level=1

def topBottom():
  geometry = SplineGeometry()
  
  # point coordinates ...
  pnts = [ (0,0), (1,0),  (1,0.5), (1,1), (0,1), (0, 0.5)]
  pnums = [geometry.AppendPoint(*p) for p in pnts]
  # start-point, end-point, boundary-condition, domain on left side, domain on right side:
  lines = [ (pnums[0],pnums[1],"gammaD",2,0), (pnums[1],pnums[2],"gammaD",2,0), 
       (pnums[2],pnums[3],"gammaS",1,0), (pnums[3],pnums[4],"gammaS",1,0),
       (pnums[4],pnums[5],"gammaS",1,0),
       (pnums[5],pnums[0],"gammaD",2,0), (pnums[5],pnums[2],"gammaSD",1,2)]
  for p1,p2,bc,left,right in lines:
      geometry.Append( ["line", p1, p2], bc=bc, leftdomain=left, rightdomain=right)
  return geometry

def GetInterfaceIndicator(mesh):
  dom_indicator = GridFunction(L2(mesh,order=0))
  dom_indicator.Set(CoefficientFunction([1,2]))
  
  ffes = FacetFESpace(mesh,order=0)
  dom_ind_average = GridFunction(ffes)
  mf = BilinearForm(ffes,symmetric=True)
  mf += SymbolicBFI(ffes.TrialFunction()*ffes.TestFunction(),element_boundary=True)
  mf.Assemble()
  ff = LinearForm(ffes)
  ff += SymbolicLFI(dom_indicator*ffes.TestFunction(),element_boundary=True)
  ff.Assemble()
  dom_ind_average.vec.data = mf.mat.Inverse() * ff.vec

  interface_indicator = BitArray(ffes.ndof)
  for i in range(len(dom_ind_average.vec)):
    if (dom_ind_average.vec[i] > 1.75) or (dom_ind_average.vec[i] < 1.25):
      interface_indicator[i] = False
    else:
      interface_indicator[i] = True
  print(sum(interface_indicator))
  return interface_indicator

def GetFaceIndicator(mesh):
  dom_indicator = GridFunction(L2(mesh,order=0))
  dom_indicator.Set(CoefficientFunction([1,2]))
  
  ffes = FacetFESpace(mesh,order=0)
  dom_ind_average = GridFunction(ffes)
  mf = BilinearForm(ffes,symmetric=True)
  mf += SymbolicBFI(ffes.TrialFunction()*ffes.TestFunction(),element_boundary=True)
  mf.Assemble()
  ff = LinearForm(ffes)
  ff += SymbolicLFI(dom_indicator*ffes.TestFunction(),element_boundary=True)
  ff.Assemble()
  dom_ind_average.vec.data = mf.mat.Inverse() * ff.vec

  stokes_indicator = BitArray(ffes.ndof)
  darcy_indicator = BitArray(ffes.ndof)
  for i in range(len(dom_ind_average.vec)):
    if (dom_ind_average.vec[i] > 1.75): # exclude darcy part
      stokes_indicator[i] = False
    else:
      stokes_indicator[i] = True
    if (dom_ind_average.vec[i] < 1.25): # exclude darcy part
      darcy_indicator[i] = False
    else:
      darcy_indicator[i] = True
  #print("facets marked as stokes facets:", stokes_indicator)
  #print("facets marked as darcy facets:", darcy_indicator)
  return stokes_indicator, darcy_indicator


stokesId = [1,0]
darcyId = [0,1]

nu = 1.
kinv = 1.
gamma = (1.+4.*pi*pi)/2.
order = 4
hmax = 0.5
dcFlag = False
mesh = Mesh(topBottom().GenerateMesh (maxh=hmax))

n = specialcf.normal(2)
h = specialcf.mesh_size
penalty = 10*order*(order+1)/h
ndofMax = 10

orderp = order-1
l=order-1


# exact solution
u1 = sin(pi*x)*exp(y/2.)
u2 = cos(pi*x)*exp(y/2.)
uexS = CoefficientFunction((-1./2./pi/pi*u1,1./pi*u2))
uexD = CoefficientFunction((-2.*u1,1./pi*u2))
pexS = CoefficientFunction(-1./pi*u2)
pexD = CoefficientFunction(-2./pi*u2)

cst1 = 1.+nu*(-.5+1./8./pi/pi)
cst2 = -.5/pi+nu*(pi-.25/pi)
cst3 = 0.5/pi-2.*pi
stokesSource = CoefficientFunction((cst1*u1,cst2*u2))
darcySource = CoefficientFunction(cst3*u2)



dom1 = GridFunction(L2(mesh,order=0))
dom2 = GridFunction(L2(mesh,order=0))

V1 = VectorL2(mesh, order=order, dirichlet="gammaS|gammaD")

V2 = FESpace ("vectorfacet", mesh, order=order, dirichlet="gammaS",definedon = [1], flags
    ={"highest_order_dc": dcFlag})
V3 = L2(mesh, order=orderp)
V4 = FESpace("number",mesh)

V = FESpace([V1,V2, V3,V4], flags={"dgjumps": True})
u,uhat, p, pbar = V.TrialFunction()
v,vhat, q, qbar = V.TestFunction()
crossTerm = -div(u)*q-div(v)*p + p*qbar + q*pbar

du = grad(u)
dv = grad(v)
gradu = CoefficientFunction ( (du,), dims=(2,2) )
gradv = CoefficientFunction ( (dv,), dims=(2,2) )
epsu = 0.5*(gradu+gradu.trans)
epsv = 0.5*(gradv+gradv.trans)

def tang(vec):
    return vec - (vec*n)*n
interface_indicator = GetInterfaceIndicator(mesh)


a = BilinearForm(V)
# dg stokes
stokesCell = 2*nu*InnerProduct(epsu,epsv)
stokesFacet1 = 2*nu*InnerProduct ( epsu*n,  tang(vhat-v) )
stokesFacet2 = 2*nu*InnerProduct ( epsv*n,  tang(uhat-u) )
stokesFacet3 = penalty*nu*InnerProduct (tang(vhat-v),tang(uhat-u) )

#darcy
darcyCell = kinv*u*v

# interface (only stokes part is needed)
interfaceTerm = gamma*sqrt(kinv)*(tang(uhat)*tang(vhat))


## DEBUGGING
# Stokes is correct
a += SymbolicBFI ( stokesCell+dom2*darcyCell + crossTerm, definedon=[1])
a += SymbolicBFI ( darcyCell + crossTerm, definedon = [2])
a += SymbolicBFI ( (stokesFacet1+stokesFacet2+stokesFacet3), element_boundary=True, definedon=[1])
# FIXME change to element_boundary 
interfacebfi = SymbolicBFI (interfaceTerm, VOL, skeleton=True) 
interfacebfi.SetDefinedOnElements(interface_indicator)
a += interfacebfi


a.Assemble()

c = Preconditioner(type="direct", bf=a, flags = { "inverse" : "pardiso" } )

f = LinearForm(V)
f += SymbolicLFI(dom1*stokesSource*v-dom2*darcySource*q)
f.Assemble()

u = GridFunction(V)
uS = GridFunction(V)
uD = GridFunction(V)
bvp =  BVP(bf=a,lf=f,gf=u,pre=c, maxsteps=1000, prec=1e-11)
vtk = VTKOutput(ma=mesh,coefs=[u.components[0],
  u.components[2]],names=["velocity","pressure"],filename="hdg",subdivision=3)
def Solve_part1():
    dom1.Update()
    dom1.Set(CoefficientFunction(stokesId))
    dom2.Update()
    dom2.Set(CoefficientFunction(darcyId))
    V.Update()
    
    interface_indicator = GetInterfaceIndicator(mesh)
    #ss, interface_indicator = GetFaceIndicator(mesh)
    interfacebfi.SetDefinedOnElements(interface_indicator)
    
    a.Assemble()
    f.Assemble()
    u.Update()
    uS.Update()
    uD.Update()
    #uS.components[0].Set(uexS,definedon=mesh.Boundaries("gammaS"))
    #uS.components[1].Set(uexS,definedon=mesh.Boundaries("gammaS"))
    #uD.components[0].Set(uexD,definedon=mesh.Boundaries("gammaD"))
    #u.vec.data = uS.vec+uD.vec
    u.components[0].Set(dom1*uexS+dom2*uexD)
    u.components[1].Set(uexS,definedon=mesh.Boundaries("gammaS"))

    #res = f.vec.CreateVector()
    #res.data = f.vec - a.mat*u.vec
    #u.vec.data += a.mat.Inverse(V.FreeDofs()) * res
    bvp.Do()
    uS.components[0].Set(dom1*uexS+dom2*uexD)
    uD.vec.data = uS.vec-u.vec
    #Draw(uD.components[0])
    errS = dom1*(u.components[0]-uexS)*(u.components[0]-uexS)
    errD = dom2*(u.components[0]-uexD)*(u.components[0]-uexD)
    erru1 = Integrate(errS,mesh,order = 2*order)
    erru2 = Integrate(errD,mesh,order = 2*order)
    return u.components[0] 
#Solution part 1 is input of part 2

#Part 2
Tend = 0.1 # End time
t = Parameter(0.0)
# c exact
cexact = CoefficientFunction(sin(2*pi*(x-t))*cos(2*pi*(y-t)))
c0  = CoefficientFunction(sin(2*pi*(x))*cos(2*pi*(y)))
Du = CoefficientFunction((0.01, 0.005, 0.005, 0.02), dims=(2,2))

#u: Approximated solution from the previous S-D problem

def SetUp_part2(mesh, u):
    
    C    = L2(mesh, order=l)
    Cbar = FacetFESpace(mesh, order=l) 
    X    = FESpace([C, Cbar])

    c, cbar = X.TrialFunction()
    w, wbar = X.TestFunction()


# Penalty parameter
    beta_c = 6*l**2
    
    n = specialcf.normal(mesh.dim)
    h = specialcf.mesh_size
    
# Bilinear Form
    a = BilinearForm(X)
    B_dx = -(c*u)*grad(w)+Du*grad(c)*grad(w)
    B_ds = (-u*c + Du*grad(c)-(IfPos(u*n,0,1)*u-(beta_c*Du)/h*n)*(cbar-c))*n*(wbar-w)\
           - (Du*grad(w))*n*(c-cbar)
    
    a += B_dx * dx
    a += B_ds * dx(element_boundary=True)
    ##error here
    a += IfPos(u*n,1,0)*(u*n)*wbar.Trace()*cbar.Trace()*ds

# Mstar = M + theta*dt*A
    m = BilinearForm(X)
    m += c*w*dx(definedon=mesh.Materials("stokesregion"))
    #m.Assemble()

# Linear form
    f = LinearForm(X)  
      
    gfu = GridFunction(X) 
   

    return (gfu, a, f, m) 

output = []
def Solve_part2(mesh, gfu, a, f, m, dt): 

    #Linear forms
    a.Assemble()
    #f.Assemble()
    m.Assemble()
    mstar = m.mat.CreateMatrix()
    mstar.AsVector().data = m.mat.AsVector() + dt * a.mat.AsVector()
    invmstar = mstar.Inverse(freedofs=gfu.space.FreeDofs(), inverse="umfpack")
    gfu.components[0].Set(c0)

    res = gfu.vec.CreateVector()
    for it in range(1,int(Tend/dt + 1)):
        
        t.Set(it*dt)
        f.Assemble()

        res.data = - dt*a.mat*gfu.vec + dt*f.vec  
        gfu.vec.data += invmstar * res 
        c=gfu.components[0]
#   
    sol = sqrt(Integrate((c)**2, mesh))
    print("\n test:", sol)
    

  
dt=0.01
for i in range(1):
        u1 = Solve_part1()
        print("u1",u1)
        #test with exact solution
        #u1=dom1*uexS+dom2*uexD
        gfu, a, f, m = SetUp_part2(mesh,u1)
        Solve_part2(mesh, gfu, a, f, m, dt)
        



2
2
u1 gridfunction 'gfu.1' on space 'CompoundFESpaces'
nested = 0


 test: 2.5245085732824952e-33
